In [1]:
import os
import shutil
import torch
import torch.nn as nn
import sys
import random
import numpy as np
from models.cifar_quant import cifar10_quantqf
import models.testset as ts
from models.train import *
import pickle
from models.tests import TestBench as TB
from models.quant_back import Conv2dQ, Conv2dQB

def dump_vars(filename, **vars):
    with open(filename, 'wb') as f:
        pickle.dump(vars, f)

if not os.path.exists('result'):
    os.makedirs('result')


cuda_device = 1
os.environ['CUBLAS_WORKSPACE_CONFIG'] = ':4096:8'
torch.manual_seed(0)
random.seed(0)
np.random.seed(0)
torch.use_deterministic_algorithms(True)
torch.backends.cudnn.deterministic = True
torch.cuda.set_device(cuda_device)
tsname = 'R32_LU_4X'

Files already downloaded and verified
Files already downloaded and verified


In [7]:
params = [
      {'lr': 2e-3, 'nhist': 1, 'epoch': 5},
      {'lr': 2e-3, 'nhist': 5, 'epoch': 10},
      {'lr': 4e-4, 'nhist': 5, 'epoch': 20},
      {'lr': 2e-3, 'nhist': 10, 'epoch': 100},
      {'lr': 2e-3, 'nhist': 10, 'epoch': 200}
]
fbits = [2, 3, 4]
gbits = [2, 3, 4, 5, 6, 7]
#cl = {'Mean': lambda x: x.abs().mean(), '2xMean': lambda x: x.abs().mean() * 2, '3xMean': lambda x: x.abs().mean() * 3}
cl = { 'Max/4': lambda x: x.abs().max() / 4, 'Max/2': lambda x: x.abs().max(), '.75Max': lambda x: x.abs().max() * 0.75, 'Max': lambda x: x.abs().max()} 

oparams = {'weight_decay': 1e-4, 'momentum': 0.9} # {'M': {'weight_decay': 1e-4, 'momentum': 0.9}, 'N': {'weight_decay': 0, 'momentum': 0}}
#epochs = [10]
best_prec = 0
criterion = nn.CrossEntropyLoss().cuda()
loaded = torch.load(f'result/CIFAR10_ORG/model_best.pth.tar', map_location={'cuda:1': f'cuda:{cuda_device}'})


In [8]:


def getopt(x, *kargs, **kwargs):
    return torch.optim.SGD(x.parameters(), **kwargs)

tbs = []


for p in params:
    for f in fbits:
        for g in gbits:
            for c in cl:
                TBx = TB(f'{f}/{g}/{c}/{p["epoch"]}', validate_training_sep, criterion,
                        getopt=lambda x, y, lr=p['lr'], p=oparams: getopt(x, lr=lr, **p), nhist=p['nhist'], n_epoch=p['epoch'], trf_eval=trf_norm, trf_train=trf_train_norm)
                TBx.f = f
                TBx.g = g
                TBx.c = cl[c]
                tbs.append(TBx)


In [9]:

for tb in tbs:
    model = cifar10_quantqf()
    model.cuda()
    model.load_state_dict(loaded['state_dict'])
    func = Conv2dQB(4, 3, tb.f, tb.f-1, tb.g, 0, tb.c)
    with torch.no_grad():
        model.recursive_do('update_func', func)
    result[tb.name] = tb.run(ts.test_pld_sets[tsname], model)
    del model

Sequential(
  (0): QuantConv2df(3, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (2): ReLU()
  (3): QuantConv2df(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (4): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (5): ReLU()
  (6): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (7): QuantConv2df(128, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (8): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (9): ReLU()
  (10): QuantConv2df(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (11): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (12): ReLU()
  (13): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (14): QuantConv2df(256, 512, kernel_

Time 49.90238690376282	Epoch: 100	Loss 0.0609	Prec 98.203
Time 50.4098424911499	Epoch: 101	Loss 0.0464	Prec 98.438
Time 50.91453003883362	Epoch: 102	Loss 0.0705	Prec 97.969
Time 51.44087553024292	Epoch: 103	Loss 0.0425	Prec 98.672
Time 51.96003985404968	Epoch: 104	Loss 0.0428	Prec 99.453
Time 52.45027041435242	Epoch: 105	Loss 0.0531	Prec 98.750
Time 52.96773672103882	Epoch: 106	Loss 0.0714	Prec 98.125
Time 53.481234073638916	Epoch: 107	Loss 0.0392	Prec 99.141
Time 53.994531869888306	Epoch: 108	Loss 0.0362	Prec 99.453
Time 54.48589563369751	Epoch: 109	Loss 0.0448	Prec 98.672
Time 54.96633791923523	Epoch: 110	Loss 0.0381	Prec 98.594
Time 55.46491265296936	Epoch: 111	Loss 0.0362	Prec 99.219
Time 55.96996593475342	Epoch: 112	Loss 0.0507	Prec 98.750
Time 56.4983172416687	Epoch: 113	Loss 0.0355	Prec 98.984
Time 57.009016275405884	Epoch: 114	Loss 0.0372	Prec 99.219
Time 57.51139521598816	Epoch: 115	Loss 0.0440	Prec 98.906
Time 58.01678276062012	Epoch: 116	Loss 0.0349	Prec 99.297
Time 58.50647

Time 14.320380449295044	Epoch: 28	Loss 0.2597	Prec 91.562
Time 14.805692672729492	Epoch: 29	Loss 0.2275	Prec 92.500
Time 15.289717197418213	Epoch: 30	Loss 0.2543	Prec 91.562
Time 15.774688005447388	Epoch: 31	Loss 0.2034	Prec 94.219
Time 16.257489681243896	Epoch: 32	Loss 0.2068	Prec 93.750
Time 16.740899562835693	Epoch: 33	Loss 0.2009	Prec 93.281
Time 17.24800944328308	Epoch: 34	Loss 0.2691	Prec 91.250
Time 17.75996446609497	Epoch: 35	Loss 0.1430	Prec 94.922
Time 18.241554975509644	Epoch: 36	Loss 0.1584	Prec 95.234
Time 18.73704767227173	Epoch: 37	Loss 0.1251	Prec 95.938
Time 19.22423791885376	Epoch: 38	Loss 0.1966	Prec 93.047
Time 19.70777940750122	Epoch: 39	Loss 0.1450	Prec 95.391
Time 20.194966793060303	Epoch: 40	Loss 0.1684	Prec 94.531
Time 20.688231945037842	Epoch: 41	Loss 0.1314	Prec 95.234
Time 21.171743154525757	Epoch: 42	Loss 0.1530	Prec 94.766
Time 21.6697838306427	Epoch: 43	Loss 0.1698	Prec 94.062
Time 22.15617084503174	Epoch: 44	Loss 0.1412	Prec 95.234
Time 22.64436578750610

Time 84.39102721214294	Epoch: 171	Loss 0.0185	Prec 99.609
Time 84.87887811660767	Epoch: 172	Loss 0.0221	Prec 99.766
Time 85.37595725059509	Epoch: 173	Loss 0.0196	Prec 99.844
Time 85.88023233413696	Epoch: 174	Loss 0.0158	Prec 99.844
Time 86.3942449092865	Epoch: 175	Loss 0.0192	Prec 99.844
Time 86.90135025978088	Epoch: 176	Loss 0.0291	Prec 99.219
Time 87.3926293849945	Epoch: 177	Loss 0.0173	Prec 99.922
Time 87.87857031822205	Epoch: 178	Loss 0.0156	Prec 99.844
Time 88.36236119270325	Epoch: 179	Loss 0.0160	Prec 100.000
Time 88.85337328910828	Epoch: 180	Loss 0.0148	Prec 99.844
Time 89.33935546875	Epoch: 181	Loss 0.0187	Prec 99.922
Time 89.82565808296204	Epoch: 182	Loss 0.0166	Prec 99.922
Time 90.31222438812256	Epoch: 183	Loss 0.0121	Prec 99.922
Time 90.80555891990662	Epoch: 184	Loss 0.0174	Prec 99.844
Time 91.30045318603516	Epoch: 185	Loss 0.0231	Prec 99.688
Time 91.78591346740723	Epoch: 186	Loss 0.0171	Prec 99.844
Time 92.27024006843567	Epoch: 187	Loss 0.0195	Prec 99.766
Time 92.7546467781

Time 49.81315302848816	Epoch: 100	Loss 0.0368	Prec 99.609
Time 50.29878854751587	Epoch: 101	Loss 0.0224	Prec 99.688
Time 50.7864146232605	Epoch: 102	Loss 0.0241	Prec 99.766
Time 51.27060413360596	Epoch: 103	Loss 0.0274	Prec 99.609
Time 51.76136922836304	Epoch: 104	Loss 0.0272	Prec 99.766
Time 52.248164892196655	Epoch: 105	Loss 0.0493	Prec 98.594
Time 52.73405885696411	Epoch: 106	Loss 0.0315	Prec 99.609
Time 53.220073223114014	Epoch: 107	Loss 0.0290	Prec 99.297
Time 53.702627182006836	Epoch: 108	Loss 0.0319	Prec 99.219
Time 54.19113111495972	Epoch: 109	Loss 0.0234	Prec 99.609
Time 54.67733812332153	Epoch: 110	Loss 0.0203	Prec 99.844
Time 55.160141706466675	Epoch: 111	Loss 0.0200	Prec 100.000
Time 55.648085594177246	Epoch: 112	Loss 0.0222	Prec 99.844
Time 56.1474027633667	Epoch: 113	Loss 0.0393	Prec 98.906
Time 56.63376045227051	Epoch: 114	Loss 0.0200	Prec 99.922
Time 57.11739778518677	Epoch: 115	Loss 0.0257	Prec 99.609
Time 57.61427855491638	Epoch: 116	Loss 0.0285	Prec 99.453
Time 58.10

...

Time 26.38734221458435	Epoch: 52	Loss 0.0459	Prec 98.906
Time 26.87254309654236	Epoch: 53	Loss 0.0281	Prec 99.609
Time 27.351893424987793	Epoch: 54	Loss 0.0337	Prec 99.219
Time 27.832407474517822	Epoch: 55	Loss 0.0345	Prec 99.141
Time 28.314011812210083	Epoch: 56	Loss 0.0259	Prec 99.844
Time 28.793920040130615	Epoch: 57	Loss 0.0228	Prec 99.688
Time 29.27830195426941	Epoch: 58	Loss 0.0224	Prec 99.531
Time 29.761536359786987	Epoch: 59	Loss 0.0315	Prec 99.219
Time 30.242411613464355	Epoch: 60	Loss 0.0236	Prec 99.688
Time 30.72240948677063	Epoch: 61	Loss 0.0388	Prec 99.219
Time 31.20460796356201	Epoch: 62	Loss 0.0329	Prec 99.141
Time 31.700534343719482	Epoch: 63	Loss 0.0264	Prec 99.609
Time 32.21067714691162	Epoch: 64	Loss 0.0220	Prec 99.531
Time 32.71929883956909	Epoch: 65	Loss 0.0211	Prec 99.609
Time 33.23522090911865	Epoch: 66	Loss 0.0146	Prec 99.844
Time 33.75129818916321	Epoch: 67	Loss 0.0252	Prec 99.453
Time 34.25610899925232	Epoch: 68	Loss 0.0304	Prec 99.531
Time 34.73968052864075	E

Time 94.66177248954773	Epoch: 193	Loss 0.0082	Prec 99.922
Time 95.14638447761536	Epoch: 194	Loss 0.0087	Prec 99.922
Time 95.62560701370239	Epoch: 195	Loss 0.0072	Prec 99.922
Time 96.10701966285706	Epoch: 196	Loss 0.0081	Prec 100.000
Time 96.58631896972656	Epoch: 197	Loss 0.0062	Prec 100.000
Time 97.06874251365662	Epoch: 198	Loss 0.0070	Prec 100.000
Time 97.55071377754211	Epoch: 199	Loss 0.0074	Prec 99.922
Test: [59/79]	Epoch: 199	Time 97.551 (97.470)	Loss 0.0053 (0.0074)	Prec 100.000% (99.922%)
Initial: [60/79]	Loss 1.2278259992599487	Prec 78.90625
Initial: [61/79]	Loss 1.0172101259231567	Prec 81.25
Initial: [62/79]	Loss 0.8022874593734741	Prec 82.8125
Initial: [63/79]	Loss 0.7910484671592712	Prec 85.15625
Initial: [64/79]	Loss 1.1574245691299438	Prec 78.90625
Initial: [65/79]	Loss 1.0157123804092407	Prec 78.90625
Initial: [66/79]	Loss 1.0917319059371948	Prec 82.03125
Initial: [67/79]	Loss 1.1077202558517456	Prec 77.34375
Initial: [68/79]	Loss 0.8956064581871033	Prec 82.8125
Initial: [

Time 59.602577924728394	Epoch: 122	Loss 0.0102	Prec 99.844
Time 60.08657383918762	Epoch: 123	Loss 0.0134	Prec 99.844
Time 60.56890416145325	Epoch: 124	Loss 0.0072	Prec 100.000
Time 61.05088138580322	Epoch: 125	Loss 0.0088	Prec 100.000
Time 61.531461000442505	Epoch: 126	Loss 0.0100	Prec 100.000
Time 62.01282739639282	Epoch: 127	Loss 0.0093	Prec 99.922
Time 62.499507665634155	Epoch: 128	Loss 0.0080	Prec 99.922
Time 62.981401443481445	Epoch: 129	Loss 0.0132	Prec 99.844
Time 63.4634804725647	Epoch: 130	Loss 0.0101	Prec 99.922
Time 63.9429829120636	Epoch: 131	Loss 0.0073	Prec 100.000
Time 64.42478919029236	Epoch: 132	Loss 0.0094	Prec 99.844
Time 64.90484833717346	Epoch: 133	Loss 0.0095	Prec 100.000
Time 65.38665175437927	Epoch: 134	Loss 0.0080	Prec 100.000
Time 65.86607694625854	Epoch: 135	Loss 0.0069	Prec 100.000
Time 66.3497622013092	Epoch: 136	Loss 0.0117	Prec 100.000
Time 66.83187079429626	Epoch: 137	Loss 0.0069	Prec 100.000
Time 67.31509327888489	Epoch: 138	Loss 0.0100	Prec 100.000
Tim

Time 21.479264497756958	Epoch: 50	Loss 0.0420	Prec 99.038
Time 21.895134687423706	Epoch: 51	Loss 0.0228	Prec 99.808
Time 22.312552213668823	Epoch: 52	Loss 0.0337	Prec 99.423
Time 22.731043100357056	Epoch: 53	Loss 0.0199	Prec 100.000
Time 23.14605140686035	Epoch: 54	Loss 0.0214	Prec 99.808
Time 23.567973613739014	Epoch: 55	Loss 0.0224	Prec 99.712
Time 23.99222421646118	Epoch: 56	Loss 0.0256	Prec 99.615
Time 24.411569833755493	Epoch: 57	Loss 0.0259	Prec 99.519
Time 24.831268072128296	Epoch: 58	Loss 0.0279	Prec 99.615
Time 25.25127625465393	Epoch: 59	Loss 0.0293	Prec 99.519
Time 25.669367790222168	Epoch: 60	Loss 0.0218	Prec 99.808
Time 26.087401866912842	Epoch: 61	Loss 0.0271	Prec 99.423
Time 26.51227569580078	Epoch: 62	Loss 0.0283	Prec 99.327
Time 26.931437969207764	Epoch: 63	Loss 0.0187	Prec 99.904
Time 27.347767114639282	Epoch: 64	Loss 0.0228	Prec 99.615
Time 27.763601541519165	Epoch: 65	Loss 0.0281	Prec 99.615
Time 28.182620525360107	Epoch: 66	Loss 0.0145	Prec 100.000
Time 28.60135173

Time 80.93252682685852	Epoch: 191	Loss 0.0055	Prec 100.000
Time 81.35219669342041	Epoch: 192	Loss 0.0074	Prec 100.000
Time 81.76508736610413	Epoch: 193	Loss 0.0067	Prec 100.000
Time 82.17607474327087	Epoch: 194	Loss 0.0070	Prec 100.000
Time 82.59389615058899	Epoch: 195	Loss 0.0054	Prec 100.000
Time 83.00825810432434	Epoch: 196	Loss 0.0071	Prec 100.000
Time 83.42148041725159	Epoch: 197	Loss 0.0076	Prec 100.000
Time 83.83687210083008	Epoch: 198	Loss 0.0062	Prec 100.000
Time 84.25470757484436	Epoch: 199	Loss 0.0084	Prec 100.000
Test: [78/79]	Epoch: 199	Time 84.255 (95.732)	Loss 0.0011 (0.0084)	Prec 100.000% (100.000%)
 * Prec 80.270%


In [10]:
dump_vars('Quant_Incremental_Parameter_Sweep_Max.txt', result=result)

In [6]:
{x: result[x][0] for x in result}

{'2/2/Max/4/5': 76.68,
 '2/2/Max/2/5': 76.63,
 '2/2/.75Max/5': 76.63,
 '2/2/Max/5': 76.26,
 '2/3/Max/4/5': 76.49,
 '2/3/Max/2/5': 76.61,
 '2/3/.75Max/5': 76.76,
 '2/3/Max/5': 76.76,
 '2/4/Max/4/5': 76.54,
 '2/4/Max/2/5': 76.63,
 '2/4/.75Max/5': 76.94,
 '2/4/Max/5': 76.75,
 '2/5/Max/4/5': 76.66,
 '2/5/Max/2/5': 76.83,
 '2/5/.75Max/5': 76.84,
 '2/5/Max/5': 76.65,
 '2/6/Max/4/5': 76.75,
 '2/6/Max/2/5': 76.83,
 '2/6/.75Max/5': 77.01,
 '2/6/Max/5': 76.46,
 '2/7/Max/4/5': 76.66,
 '2/7/Max/2/5': 76.94,
 '2/7/.75Max/5': 76.76,
 '2/7/Max/5': 76.71,
 '3/2/Max/4/5': 77.74,
 '3/2/Max/2/5': 77.17,
 '3/2/.75Max/5': 77.5,
 '3/2/Max/5': 77.17,
 '3/3/Max/4/5': 77.45,
 '3/3/Max/2/5': 77.9,
 '3/3/.75Max/5': 77.65,
 '3/3/Max/5': 77.77,
 '3/4/Max/4/5': 77.88,
 '3/4/Max/2/5': 77.78,
 '3/4/.75Max/5': 78.15,
 '3/4/Max/5': 78.03,
 '3/5/Max/4/5': 78.04,
 '3/5/Max/2/5': 77.89,
 '3/5/.75Max/5': 78.1,
 '3/5/Max/5': 78.01,
 '3/6/Max/4/5': 78.15,
 '3/6/Max/2/5': 78.47,
 '3/6/.75Max/5': 78.33,
 '3/6/Max/5': 78.3,
 '3